<a id="top" style="float:left;" href="http://dynfluid.ensam.eu/"><img style="height:100px;" src="https://hpp.education/Lessons/omnes-docet-ubique.png"/></a>
<a style="float:right;" href="http://www.cnam.fr//"><img style="height:80px;" src="https://upload.wikimedia.org/wikipedia/commons/6/66/Logo_cnam.gif"/></a>
<center></center>

<center>
<h3 style="color:#888888;"> <i>--  Simulation numérique en mécanique des fluides  --</i> </h3>
<h1> TP n°6</h1>
<h3> Etude de stabilité numérique </h3>
<h4>  </h4>
<h6><a href="mailto:simon.marie@lecnam.net">simon.marie@lecnam.net</a></h6>
</center>

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
# la librairie time nous sera utile pour calculer le temps d'execution des scripts
import time 
#Option pour afficher les figures dans le notebook et eviter le plt.show():
%matplotlib inline   

On se propose dans ce TP, de revenir sur les schémas étudiés dans les TP 4 et 5 en étudiant leur stabilité numérique et leur dissipation. L'équation de départ sera la même:

$$
\displaystyle{\dfrac{\partial f}{\partial t}+V_0\dfrac{\partial f}{\partial x}=0}
$$


# 1 - Synthèse des TP 4 et 5

On pourra reprendre les paramètres et les fonctions définies dans les TP précédent que l'on pourra importer par copier/coller:

In [ ]:
#Definition des parametres:
V0=5
Lambda=10
k=2*np.pi/Lambda
omega=k*V0

#On imppose dx:
dx=0.1
Nppw=Lambda/dx
x=np.arange(-100,100,dx)


def init(dx):
    k=2.*np.pi/Lambda
    Nppw=Lambda/dx
    x=np.arange(-100,100,dx)
    finit=np.exp(-(x+40.)**2/50.)*np.sin(k*x)
    return x,finit

def ref_th(t,dx=0.1):
    k=2.*np.pi/Lambda
    omega=k*V0
    xth=np.arange(-100,100,dx)
    fth=np.exp(-(xth+40.-V0*t)**2/50.)*np.sin(k*xth-omega*t)
    return xth,fth


In [ ]:
def Solve_explicit_cent(C,dx,Nt):
    x,f=init(dx)
    t0=time.time()
    for t in range(Nt):
        fn=f.copy()
        for j in range(1,len(x)-1):
            f[j]=fn[j]-0.5*C*(fn[j+1]-fn[j-1])
    t=time.time()-t0  
    return x,f,t

def Solve_explicit_decent(C,dx,Nt):
    x,f=init(dx)
    t0=time.time()
    for t in range(Nt):
        fn=f.copy()
        for j in range(1,len(x)-1):
            f[j]=fn[j]-C*(fn[j]-fn[j-1])
    t=time.time()-t0  
    return x,f,t

def Solve_implicit_cent(C,dx,Nt):
    x,f0=init(dx)
    t0=time.time()
    A=np.diag(np.ones(len(f0)))+0.5*C*np.diag(np.ones(len(f0)-1),1)-0.5*C*np.diag(np.ones(len(f0)-1),-1)
    Am1=np.linalg.matrix_power(A,-Nt)
    f=np.dot(Am1,f0)
    t=time.time()-t0  
    return x,f,t

def Solve_implicit_decent(C,dx,Nt):
    x,f0=init(dx)
    t0=time.time()
    A=(1+C)*np.diag(np.ones(len(f0)))-C*np.diag(np.ones(len(f0)-1),-1)
    Am1=np.linalg.matrix_power(A,-Nt)
    f=np.dot(Am1,f0)
    t=time.time()-t0  
    return x,f,t


<h1> 2 - Etude de la stabilité numérique</h1>

Après avoir complété les fonctions précédentes, on peut maintenant comparer les résultats des 4 schémas suivants:

1. Schéma explicite centré
2. Schéma explicite décentre amont
3. Schéma implicite centré
4. Schéma implicite décentré amont

On peut alors définir une fonction ayant pour argument, le nombre de Courant: $CFL=\mathcal{C}=V_0\dfrac{\Delta t}{\Delta x}$, le pas d'espace $dx$ et le nombre d'itération $N_t$:

In [ ]:
def plot_comp(C,dx,Nt):
    # Temps atteint pour Nt itération:
    t=...
    fig = plt.figure(figsize=(16,4));
    x,f,tc=Solve_explicit_cent(C,dx,Nt);plt.plot(x,f,label='Explicite centré t='+str(round(tc,2))+'s')
    x,f,tc=Solve_explicit_decent(C,dx,Nt);plt.plot(x,f,label='Explicite décentré t='+str(round(tc,2))+'s')
    x,f,tc=Solve_implicit_cent(C,dx,Nt);plt.plot(x,f,label='Implicite centré t='+str(round(tc,2))+'s')
    x,f,tc=Solve_implicit_decent(C,dx,Nt);plt.plot(x,f,label='Implicite décentré t='+str(round(tc,2))+'s')
    x,f=ref_th(t,dx=0.1);plt.plot(x,f,'--k',label='Ref th')
    plt.ylim(-1,1)
    plt.grid()
    plt.legend(fontsize=16)

En utilisant les élémetns de cours vus dans le chapitre 5, comparer les résultats des 4 schémas et retrouver les principaux résultats théorique sur la stabilité des différents schémas.

## Variation de la résolution:

Comparer les schémas pour un CFL de 0.8, $N_t=200$ et différentes valeurs de $dx$

In [ ]:
plot_comp(0.8,0.5,200)

In [ ]:
plot_comp(0.8,0.25,200)

In [ ]:
plot_comp(0.8,0.1,200)

**Discussions:**





--

## Variation du CFL

Faire varier le CFL en gardant les autres paramètres constant:

In [ ]:
plot_comp(0.8,0.2,100)

In [ ]:
plot_comp(1.,0.2,100)

In [ ]:
plot_comp(1.6,0.2,100)

**Discussions:**





--

<h1> 3 - Analyse de la dissipation </h1> 

## Dissipation numérique

L'erreur numérique obtenue pour une résolution donnée, se traduit ici sous la forme d'une perte d'"énergie" du paquet d'onde. Afin de quantifier cette perte d'énergie, on peut définir une fonction qui calcul le ratio entre l'énergie de la solution numérique et celle de la solution théorique en définissant l'énergie $\mathcal{E}$ de la solution $f$ sur le domaine $\mathcal{D}$ sous la forme:

$$
\mathcal{E}=\sqrt{\int_\mathcal{D}f^2 dx}
$$

In [ ]:
def ratio(C,dx,Nt):
    dt=...
    xth,fth=ref_th(Nt*dt,dx)
    x,f,t=Solve_explicit_decent(C,dx,Nt)
    E_num=...
    E_th=...
    return E_num/E_th

**Calculer numériquement l'évolution de la dissipation $\dfrac{\mathcal{E}_{num}}{\mathcal{E}_{th}}$ en fonction de la résolution**


Attention, il faut s'assurer que la perturbation reste bien dans le domaine, donc que la distance parcourue par celle-ci reste plus petite que le domaine de calcul. On prend comme limite $d=100$ ce qui nous impose:
$$
d=V_0 t=N_t CFL \Delta x \leq 100 
$$

La condition la plus contraignante est obtenue pour la plus grande valeur de $\Delta x=2$ (qui correspond à $N_{ppw}=\dfrac{\lambda}{\Delta x}=5$ points par longueur d'ondes) ce qui impose la contrainte:
$$
N_t CFL\leq 50
$$

On choisit par exemple $N_t=100$ et $CFL=0.5$
On peut faire ça dans une boucle:

In [ ]:
Npp_vec=np.linspace(5,50,10)
Ratios=np.zeros(10)

for i,npp in enumerate(Npp_vec):
    dx=Lambda/npp
    Ratios[i]=ratio(0.5,dx,100)

In [ ]:
plt.plot(Npp_vec,Ratios)
plt.xlabel('$N_{ppw}$')
plt.ylabel('$E_{num}/E_{th}$')

**Discussions**



---------

## Dissipation théorique

Dans l'exercice 14 du poly, nous avons montré que le facteur d'amplification du schéma décentré amont pouvait s'exprimer sous la forme:

$$
G=\dfrac{\epsilon_i^{n+1}}{\epsilon_i^n}=1-\mathcal{C}+\mathcal{C}\cos\left(\dfrac{2\pi}{N_{ppw}}\right)-j\mathcal{C}\sin\left(\dfrac{2\pi}{N_{ppw}}\right)
$$

Nous avons également montré que la dissipation d'un schéma était liée au module du facteur d'amplification $|G|$. Ainsi on peut retrouver la dissipation de la perturbation au bout de $N_t$ itérations en calculant $|G|^{N_t}$.



In [ ]:
C=0.5;Nt=100;
partie_Re=...
partie_Im=...
G=partie_Re+1j*partie_Im

In [ ]:
plt.plot(Npp_vec,np.abs(G)**Nt)
plt.plot(Npp_vec,Ratios,'^k')
plt.xlabel('$N_{ppw}$')
plt.ylabel('$E_{num}/E_{th}$')

**Discussions**




---


**On pourra ensuite comparer avec la dissipation des schémas implicites**


# Conclusion

Présenter un synthèse des résultats obtenus dans ce TP.

In [18]:
from IPython.core.display import HTML
style=open('notebooks.css', "r").read()
HTML(style)

<a id="top" style="float:left;" href="http://dynfluid.ensam.eu/"><img style="height:100px;" src="https://hpp.education/Lessons/omnes-docet-ubique.png"/></a>
<a style="float:right;" href="http://www.cnam.fr//"><img style="height:80px;" src="https://upload.wikimedia.org/wikipedia/commons/6/66/Logo_cnam.gif"/></a>
<center></center>
<center><a href="#top">Retour en haut de la page</a></center>